# **I Want To Buy A House Map**

#### In the near future, I intend to buy a house. 
#### I also intend to buy an electric car. 
Naturally, this led me down the path of creating a map visualisation of the shapefile of local authority boundaries in England, combined with data for the mean annual house price in England and how many electric vehicle charging stations were in each local authority. Because this is the only sensible way for me to come to a decision on the best place to make my largest investment yet.

## Import the relevant libraries

In [1]:
import folium
import pandas as pd
import geopandas as gpd
import requests
import pandas_geojson as pdg
import json



## Creating the map

In [2]:
m = folium.Map(width=900, height=500,location=[52.3555, 1.1743],zoom_start = 6, tiles = "OpenStreetMap" )
m

## Reading in the geojson version of the local authority boundaries (EW) shapefile

In [3]:
filename = 'local_authorities_espg_4326.geojson'

#make the geojson file a geopandas dataframe
gpd_df = gpd.read_file(filename, driver = 'geojson')
gpd_df.head(2) 

LAD23CD        LAD23NM LAD23NMW   BNG_E   BNG_N     LONG      LAT  \
0  E06000001     Hartlepool     None  447160  531474 -1.27018  54.6761   
1  E06000002  Middlesbrough     None  451141  516887 -1.21099  54.5447   

                               GlobalID  \
0  30c07a92-d72e-4cb0-8670-82730983c395   
1  e89cee90-7dfc-4bef-a375-ad715f00d455   

                                            geometry  
0  MULTIPOLYGON (((-1.24119 54.72334, -1.24099 54...  
1  MULTIPOLYGON (((-1.19861 54.58287, -1.16664 54...

In [4]:
# add the local authority boundaries to the map
m = folium.Map(width= 900, length= 500, location=[51.509865, -0.118092], zoom_start=6)

# Add the geopandas dataframe to the map
folium.GeoJson(data=gpd_df).add_to(m)
m

# Data cleaning and manipulation

As the data has been taken from different sources, some normalisation needs to be done to enable manipulation for useful analysis

## Reading in the electric charging station csv data

In [5]:
# making the data into a pandas dataframe
df = pd.read_csv('ev_charging_stations_clean.csv')
df.head(10)

Local Authority / Region Code Local Authority / Region Name  \
0                     K02000001                United Kingdom   
1                     K03000001                 Great Britian   
2                     E92000001                       England   
3                     E12000001                    North East   
4                     E06000047                 County Durham   
5                     E06000005                    Darlington   
6                     E06000001                    Hartlepool   
7                     E06000002                 Middlesbrough   
8                     E06000057                Northumberland   
9                     E06000003          Redcar and Cleveland   

  Jan23 Total Charging Devices Jan-23 \n(per 100,000 population)   \
0                       37,055                               55.3   
1                       36,689                               56.3   
2                       31,466                               55.7   
3                        1,253                               47.3   
4                          229                               43.9   
5                           68                               62.8   
6                           24                               25.9   
7                           51                               35.5   
8                          251                               78.1   
9                           37                               27.1   

  Oct-22\n(Total Charging Devices) Oct-22\n(per 100,000 population)   \
0                           34,637                              51.6   
1                           34,295                              52.6   
2                           29,774                              52.7   
3                            1,142                              42.6   
4                              206                              38.6   
5                               54                              50.3   
6                                8                               8.5   
7                               33                              23.4   
8                              220                              67.9   
9                               45                              32.8   

  July-22 \n(Total Charging Devices) July-22 \n(per 100,000 population)  \
0                             32,011                               47.7   
1                             31,683                               48.6   
2                             27,502                               48.6   
3                              1,155                               43.1   
4                                174                               32.6   
5                                 49                               45.6   
6                                 11                               11.7   
7                                 38                               26.9   
8                                226                               69.8   
9                                 40                               29.1   

  Apr-22 \n(Total Charging Devices) Apr-22 \n(per 100,000 population)  ...  \
0                            30,290                              45.2  ...   
1                            29,942                              45.9  ...   
2                            25,884                              45.8  ...   
3                             1,011                              37.7  ...   
4                               149                              27.9  ...   
5                                31                              28.9  ...   
6                                12                              12.8  ...   
7                                34                              24.1  ...   
8                               198                              61.1  ...   
9                                36                              26.2  ...   

  Oct-20 \n(Total Charging Devices) Oct-20 \n(pe

In [6]:
#remove null values and assign to electric vehicle charging point dataframe for 2023 values
newdf= df.dropna(axis = 1, how= 'all') 
newdf= newdf.dropna(axis = 0, how= 'all') 

# selecting the columns needed from data, ensure its a copy so column name can be overwritten
ev_df= newdf.iloc[:, [0,1,2]].copy()

# rename the 'Local Authority/ Region Name' column so it can be grouped by later
ev_df.rename(columns={"Local Authority / Region Name" : "Local Authority"}, inplace = True)

ev_df.head(2)

Local Authority / Region Code Local Authority Jan23 Total Charging Devices
0                     K02000001  United Kingdom                       37,055
1                     K03000001   Great Britian                       36,689

## Reading in the mean house prices England 2023 data

In [7]:
INDICATOR = 'Mean House Prices in 2023 (£)'
#import in house price index csv data
df1 = pd.read_csv('England-annual-price-change-by-local-authority-2023-06.csv',encoding='unicode_escape')

# assign to the house price index dataframe for only 2023
hpi_df = df1[["Local authorities","June 2023","Difference"]].copy()

# rename the 'Local Authority/ Region Name' column so it can be grouped by later
hpi_df.rename(columns={"Local authorities" : "Local Authority"}, inplace = True)
hpi_df.rename(columns={"June 2023" : "Mean House Price 2023"}, inplace = True)

#changing the column types
hpi_df['Local Authority'] = hpi_df['Local Authority'].astype(str)
hpi_df["Mean House Price 2023"] = hpi_df["Mean House Price 2023"].str.replace('£', '').astype(int)
hpi_df['Difference'] = hpi_df['Difference'].str.replace('%', '').astype(float)
hpi_df.head(3)

Local Authority  Mean House Price 2023  Difference
0            Adur                 378445         0.4
1    Amber Valley                 228195         6.7
2            Arun                 351693         0.4

# Interactive map visualisations

## Adding the house prices of different local authorities into a chloropleth map

In [8]:
# add to folium map
folium.Choropleth(
    geo_data = gpd_df,
    data=hpi_df,
    columns = ['Local Authority', 'Mean House Price 2023'],
    key_on = 'properties.LAD23NM',
    fill_color='YlGnBu',
    fill_opacity=1,
    line_opacity=0.2,
    legend_name= INDICATOR
).add_to(m)
m

## Merging the dataframes to create object polygons to add to the map

In [9]:
# merge the dataframes

merged_df = pd.merge(
    left = gpd_df,
    right= ev_df,
    left_on = 'LAD23NM',
    right_on = 'Local Authority',
    how= 'inner'
)

final_merge = pd.merge(
    left = merged_df,
    right= hpi_df,
    left_on = 'LAD23NM',
    right_on = 'Local Authority',
    how= 'left'
) 
final_merge.head(3)


LAD23CD               LAD23NM LAD23NMW   BNG_E   BNG_N     LONG      LAT  \
0  E06000001            Hartlepool     None  447160  531474 -1.27018  54.6761   
1  E06000002         Middlesbrough     None  451141  516887 -1.21099  54.5447   
2  E06000003  Redcar and Cleveland     None  464361  519597 -1.00608  54.5675   

                               GlobalID  \
0  30c07a92-d72e-4cb0-8670-82730983c395   
1  e89cee90-7dfc-4bef-a375-ad715f00d455   
2  a1ddad96-e6a8-4b04-9cab-098c8e1df209   

                                            geometry  \
0  MULTIPOLYGON (((-1.24119 54.72334, -1.24099 54...   
1  MULTIPOLYGON (((-1.19861 54.58287, -1.16664 54...   
2  MULTIPOLYGON (((-0.79180 54.55831, -0.80042 54...   

  Local Authority / Region Code     Local Authority_x  \
0                     E06000001            Hartlepool   
1                     E06000002         Middlesbrough   
2                     E06000003  Redcar and Cleveland   

  Jan23 Total Charging Devices     Local Authority_y  Mean House Price 2023  \
0                           24            Hartlepool               131060.0   
1                           51         Middlesbrough               136605.0   
2                           37  Redcar and Cleveland               158981.0   

   Difference  
0         2.3  
1         0.9  
2         4.5

In [10]:
# create global popup
popup = folium.GeoJsonPopup(
    fields= ['LAD23NM','Difference'],
    localize=True,
    labels=True,
    style="background-color: transparent;",
)

# create global tooltip
tooltip = folium.GeoJsonTooltip(
    fields=["LAD23NM", "Jan23 Total Charging Devices", "Difference"],
    aliases=["Local Authority Name:", "2023 Total Electric Vehicle Charging Stations:", "% Change from 2022 average:"],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """,
    max_width=800,
)

In [11]:
# add the merged dataframe to the map
g = folium.GeoJson(
    final_merge,
    style_function=lambda x: {"fillColor":"transparent"},
    tooltip=tooltip,
    popup=popup,
).add_to(m)

m

## Save to HTML file

In [12]:
m.save('iwanttobuyahousemap.html')